In [1]:
%load_ext autoreload

%autoreload 2

In [2]:
import simpleaudio as sa
import numpy as np
import os

import IPython.display as ipd

In [71]:
from pySynth.io.IO import *
from pySynth.io.player import *
from pySynth.control.stream import EffectChain, MIDIStream
from pySynth.synth.effect import *
from pySynth.synth.filter import *
from pySynth.synth.synthesizer import *
from pySynth.synth.oscillator import *

In [19]:
midi_filepath = "D:\\Documents\\2021Spring\\DSP_Final\\midi\\test.mid"

midi_func = ReadMIDI(midi_filepath)
midi_ls = midi_func()
print(midi_ls)

fs = 44100
# >>> [[60, 0.0, 0.5], [64, 0.5, 1.0], [67, 1.0, 1.5], [64, 2.0, 2.5], [62, 2.5, 2.75], 
# [60, 2.75, 3.0], [62, 3.0, 3.125], [60, 3.25, 3.375], [60, 3.5, 4.0], [69, 4.0, 4.5], 
# [67, 4.5, 5.0], [62, 5.0, 5.25], [64, 5.25, 5.5], [62, 5.5, 5.75], [62, 5.75, 6.0], 
# [64, 6.0, 6.25], [60, 6.5, 7.0], [62, 7.0, 7.5], [60, 7.5, 8.0]]

[[60, 0.0, 0.5], [64, 0.5, 1.0], [67, 1.0, 1.5], [64, 2.0, 2.5], [62, 2.5, 2.75], [60, 2.75, 3.0], [62, 3.0, 3.125], [60, 3.25, 3.375], [60, 3.5, 4.0], [69, 4.0, 4.5], [67, 4.5, 5.0], [62, 5.0, 5.25], [64, 5.25, 5.5], [62, 5.5, 5.75], [62, 5.75, 6.0], [64, 6.0, 6.25], [60, 6.5, 7.0], [62, 7.0, 7.5], [60, 7.5, 8.0]]


# Midi Input

In [20]:
normalization_factor = 1
stream = MIDIStream("sine")
audio = stream.render(midi_ls)
# audio = ((audio) / normalization_factor * 32767).astype(np.int16)

ipd.Audio(audio, rate = fs)

# OSC with ADSR

In [21]:
adsr = ADSR()
normalization_factor = 1
stream = MIDIStream("sine", adsr = adsr)
audio = stream.render(midi_ls)
audio = ((audio) / normalization_factor * 32767).astype(np.int16)

ipd.Audio(audio, rate = 44100)

# One Effect Chain

In [25]:
effects = EffectChain(
#     Reverb(1,1,"hall"),
#     Delay(delayTime = 0.25),
#     Chorus(),
    Vibrato(100, -0.5),
#     LowPass(Low_Band=800)
)

adsr = ADSR()
stream = MIDIStream("sine", adsr = adsr)
audio = stream.render(midi_ls)
audio = effects(audio)

ipd.Audio(audio, rate = fs)

# Multiple Effect Chains & AddSynth

In [26]:
effects1 = EffectChain(
    Reverb(1,1,"hall"),
    Delay(delayTime = 0.25),
)

effects2 =  EffectChain(
    Chorus(),
    BandPass(Low_Band=400)
)

stream = MIDIStream("triangle")
audio = stream.render(midi_ls)
audio1 = effects1(audio)
audio2 = effects2(audio)

synth = AddSynth(
    audio1,
    audio2)

audio = synth()

ipd.Audio(audio, rate = fs)

# Wave Table

### Use three osc for one note

In [67]:
adsr = ADSR()

stream1 = MIDIStream("sine",adsr)
stream2 = MIDIStream("triangle")
stream3 = MIDIStream("square",adsr)

wt = WaveTable(
    stream1,
    stream2,
    stream3
)

audio = wt(midi_ls)
ipd.Audio(audio, rate = fs)

# Play the music using Player object, not Jupyter Notebook's Audio gadget

In [73]:
player = Player(sr = fs, bit_depth = 16)
player.play(audio)

# Save the audio into a file

In [77]:
saveAudio("example.wav", audio, sr = fs, format = "wav", bit_depth = 16)